Ensures that Transformers and pytorch_lightning libraries are installed in the runtime.

In [2]:
%%capture
%pip install transformers
%pip install pytorch_lightning


Imports everything needed for creating the model

In [3]:
import pandas as pd
import numpy as np
from torch.utils.data import Dataset
import torch
from transformers import AutoTokenizer
import pytorch_lightning as pl
from torch.utils.data import DataLoader
from transformers import AutoModel, AdamW, get_cosine_schedule_with_warmup
import torch.nn as nn
import math
from torchmetrics.functional.classification import auroc
import torch.nn.functional as F
from transformers import BertForMaskedLM, TFBertForMaskedLM

Defines class toxicity_dataset, which extends Dataset. __init__ takes a path to the csv file, a tokenizer, a list of attributes, a maximum length for the token which defaults to 128, and a size for sampling the data which defaults to 5000.

The toxicity_dataset class prepares the data by sampling the csv file in _prepare_data, returns the length of the dataset with __len__, and can acess an item with an index and return its input ids, its attention mask, and its labels.




In [4]:
class toxicity_dataset(Dataset):
    def __init__(self,data_path,tokenizer,attributes,max_token_len= 128,sample = 5000):
        self.data_path=data_path
        self.tokenizer=tokenizer
        self.attributes=attributes
        self.max_token_len=max_token_len
        self.sample=sample
        self._prepare_data()
    def _prepare_data(self):
        data=pd.read_csv(self.data_path)
        if self.sample is not None:
            self.data=data.sample(self.sample,random_state=7)
        else:
            self.data=data
    def __len__(self):
        return(len(self.data))
    def __getitem__(self,index):
        item = self.data.iloc[index]
        comment = str(item.comment_text)
        attributes = torch.FloatTensor(item[self.attributes])
        tokens = self.tokenizer.encode_plus(comment,add_special_tokens=True,return_tensors="pt",truncation=True,max_length=self.max_token_len,padding="max_length",return_attention_mask=True)
        return{'input_ids':tokens.input_ids.flatten(),"attention_mask":tokens.attention_mask.flatten(),"labels":attributes}


Defines Toxicity_Data_Module, which extends pytorch_lightnign.LightningDataModule.__init__ takes a path to the training data set and a testing set, a list of attributes, batch size, tax token length, and the name of the model. It has methods to create and return a dataloader for training, validation, and prediciton.

In [5]:
class Toxcity_Data_Module(pl.LightningDataModule):
    def __init__(self,train_path,test_path,attributes,batch_size = 16, max_token_len = 128, model_name="roberta-base"):
        super().__init__()
        self.train_path=train_path
        self.test_path=test_path
        self.attributes=attributes
        self.batch_size=batch_size
        self.max_token_len=max_token_len
        self.model_name=model_name
        self.tokenizer = AutoTokenizer.from_pretrained(model_name)
    def setup(self, stage = None):
        if stage in (None, "fit"):
            self.train_dataset=toxicity_dataset(self.train_path,self.tokenizer,self.attributes)
            self.test_dataset=toxicity_dataset(self.test_path,self.tokenizer,self.attributes, sample=None)
        if stage == "predict":
            self.val_dataset=toxicity_dataset(self.test_path,self.tokenizer,self.attributes)
    def train_dataloader(self):
        return DataLoader(self.train_dataset,batch_size=self.batch_size,shuffle=True, num_workers=12)
    def val_dataloader(self):
        return DataLoader(self.train_dataset,batch_size=self.batch_size,shuffle=False, num_workers=12)
    def predict_dataloader(self):
        return DataLoader(self.test_dataset,batch_size=self.batch_size,shuffle=False, num_workers=12)
    

Defines Toxic_Comment_Classifier, which is the actual model we are fine tuning, and extends pl.LightningModule. __init__ takes a dictionary storing model name, number of labels, batch size, learning rate, warmup, the size of the training set, weighted decay, and number of epochs. It's methods are never called explicitly in the code, and the class is instead used by a pytorch_lightning Trainer object.

In [6]:
class Toxic_Comment_Classifier(pl.LightningModule):
  def __init__(self, config: dict):
    super().__init__()
    self.config = config
    self.pretrained_model = AutoModel.from_pretrained(config['model_name'], return_dict = True)
    self.hidden = torch.nn.Linear(self.pretrained_model.config.hidden_size, self.pretrained_model.config.hidden_size)
    self.classifier = torch.nn.Linear(self.pretrained_model.config.hidden_size, self.config['n_labels'])
    torch.nn.init.xavier_uniform_(self.classifier.weight)
    self.loss_func = nn.BCEWithLogitsLoss(reduction='mean')
    self.dropout = nn.Dropout()
    
  def forward(self, input_ids, attention_mask=None, labels=None):
    # roberta layer
    output = self.pretrained_model(input_ids=input_ids, attention_mask=attention_mask)
    pooled_output = torch.mean(output.last_hidden_state, 1)
    # final logits
    pooled_output = self.dropout(pooled_output)
    pooled_output = self.hidden(pooled_output)
    pooled_output = F.relu(pooled_output)
    pooled_output = self.dropout(pooled_output)
    logits = self.classifier(pooled_output)
    # calculate loss
    loss = 0
    if labels is not None:
      loss = self.loss_func(logits.view(-1, self.config['n_labels']), labels.view(-1, self.config['n_labels']))
    return loss, logits

  def training_step(self, batch, batch_index):
    loss, outputs = self(**batch)
    self.log("train loss ", loss, prog_bar = True, logger=True)
    return {"loss":loss, "predictions":outputs, "labels": batch["labels"]}

  def validation_step(self, batch, batch_index):
    loss, outputs = self(**batch)
    self.log("validation loss ", loss, prog_bar = True, logger=True)
    return {"val_loss": loss, "predictions":outputs, "labels": batch["labels"]}

  def predict_step(self, batch, batch_index):
    loss, outputs = self(**batch)
    return outputs

  def configure_optimizers(self):
    optimizer = AdamW(self.parameters(), lr=self.config['lr'], weight_decay=self.config['w_decay'])
    total_steps = self.config['train_size']/self.config['bs']
    warmup_steps = math.floor(total_steps * self.config['warmup'])
    warmup_steps = math.floor(total_steps * self.config['warmup'])
    scheduler = get_cosine_schedule_with_warmup(optimizer, warmup_steps, total_steps)
    return [optimizer],[scheduler]

The variable, attributes, stores the list of labels used to classify the comments. toxicity_data_module is created and setup for later use.

In [ ]:
attributes=["toxic","severe_toxic","obscene","threat","insult","identity_hate"]

toxicity_data_module=Toxcity_Data_Module("/content/sample_data/train.csv","/content/sample_data/train.csv",attributes)
toxicity_data_module.setup()

Here, we define the config dictionary. the model we are fine tuning is the distilroberta-base model. We use attributes to get the number of labels. the batch size is 128, the learning rate is 0.0000015, and we're using 80 epochs for training.

In [ ]:
config = {
    'model_name':"distilroberta-base",
    'n_labels':len(attributes),
    'bs':128,
    'lr':1.5e-6,
    'warmup':0.2,
    "train_size":len(toxicity_data_module.train_dataloader()),
    'w_decay':0.001,
    'n_epochs':80
}


We recreated toxicity_data_module using the batch size from the config file, and set it up again. The variable trainer is created as a pytorch_lightning.Trainer object, taking the number of epochs and a number of sanity validation steps. The trainer object then fits the model using the model we created and the data module. torch.save() is called to save the model into a file called model.pt, which can be loaded for later use. This is how the model was loaded into the streamlit app without having to retrain it by scratch.

In [ ]:
toxicity_data_module=Toxcity_Data_Module("/content/sample_data/train.csv","/content/sample_data/test.csv",attributes,batch_size=config['bs'])
toxicity_data_module.setup()
model = Toxic_Comment_Classifier(config)

trainer = pl.Trainer(max_epochs=config['n_epochs'],num_sanity_val_steps=50)
trainer.fit(model,toxicity_data_module)
torch.save(model, "/content/sample_data/model.pt")

After all 80 epochs, the training and validatin loss are all very low, under 0.05. This shows that the model is pretty effective at determining the labels, and is not overfitting.

Here we load the model file back into the model variable.

In [11]:
model = torch.load("/content/sample_data/model.pt")


The function predict_raw_comments() takes the model, and the data module, and gets predictions from the trainer in the form of logits.

In [12]:
def predict_raw_comments(model, dm):
  predictions = trainer.predict(model,dm)
  logits = np.stack([torch.sigmoid(torch.Tensor(p)) for batch in predictions for p in batch])
  return logits

Below, we use the predict_raw_comments() function to get the predicted logits.

In [ ]:
logits = predict_raw_comments(model,toxicity_data_module)


below, we convert the numpy array of logits retrieved into torch logits using torch.from_numpy(logits). We then use a softmax function to find the softmax probabilities for each label, and convert it back into a numpy array. 

In [ ]:
torch_logits = torch.from_numpy(logits)
probabilities = F.softmax(torch_logits, dim = -1).numpy()


We can then load our testing data into a dataframe, and use a nested loop to loop through both the input dataframe and the probabilities dataframe to find the label with the maximum probability. We can store the comment, the most likely labe, and the probability of that label into a new dataframe called results_df.

In [ ]:
inputs=pd.read_csv("/content/sample_data/test.csv")
data=[]
for i in range(20):
  max_prob = 0
  max_cat = 6
  
  prob=0
  for j in range(6):
      prob=probabilities[i][j]
      if(prob >= max_prob): 
        max_prob = prob 
        max_cat = j
  data.append([inputs["comment_text"][i],attributes[max_cat],max_prob])
results_df=pd.DataFrame(data,columns=["Comment Text","Most Likely Classification","Classification Probability"])